<a href="https://colab.research.google.com/github/jiorjioo/KelasMahir-3.0/blob/main/Balma_Bahira_Pilkada_DKI_TFIDF.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Pembersihan Data

**Import library dan package yang dibutuhkan**

In [2]:
import sys

if not sys.warnoptions:
    import warnings
    warnings.simplefilter("ignore")

In [3]:
import numpy as np
import pandas as pd
import string

**Masukkan dataset yang akan digunakan**

In [4]:
twit_sentimen = pd.read_csv('https://raw.githubusercontent.com/jiorjioo/treasure/main/dataset_tweet_sentiment_pilkada_DKI_2017.xls.csv', sep=',', encoding = 'utf-8')
twit_sentimen.head()


Id  ...                                         Text_Tweet
0   1  ...  Banyak akun kloning seolah2 pendukung #agussil...
1   2  ...  #agussilvy bicara apa kasihan yaa...lap itu ai...
2   3  ...  Kalau aku sih gak nunggu hasil akhir QC tp lag...
3   4  ...  Kasian oh kasian dengan peluru 1milyar untuk t...
4   5  ...  Maaf ya pendukung #AgusSilvy..hayo dukung #Ani...

[5 rows x 4 columns]

kolom yang kita punya: **ID, Sentiment, Pasangan_Calon, Text_Tweet**

In [5]:
tweet = twit_sentimen.Text_Tweet
paslon = twit_sentimen.Pasangan_Calon
sentimen = twit_sentimen.Sentiment

tweet

0      Banyak akun kloning seolah2 pendukung #agussil...
1      #agussilvy bicara apa kasihan yaa...lap itu ai...
2      Kalau aku sih gak nunggu hasil akhir QC tp lag...
3      Kasian oh kasian dengan peluru 1milyar untuk t...
4      Maaf ya pendukung #AgusSilvy..hayo dukung #Ani...
                             ...                        
895    Kali saja bpk @aniesbaswedan @sandiuno lihat, ...
896    Kita harus dapat merangkul semua orang tanpa b...
897    Ini jagoanku dibidang digital <Smiling Face Wi...
898                 #PesanBijak #OkeOce #GubernurGu3 ...
899    Sandiaga: Bangun Rumah DP 0% Lebih Simpel Diba...
Name: Text_Tweet, Length: 900, dtype: object

**MULAI TEXT PROCESSING**

**Proses Case Folding**

In [6]:
# CASE FOLDING

import re, string, unicodedata 

def Case_Folding(text):
    # Hapus non-ascii
    text = unicodedata.normalize('NFKD', text).encode('ascii', 'ignore').decode('utf-8', 'ignore')
    
    # Menghapus Tanda Baca
    text = re.sub(r'[^\w]|_',' ', text)
    
    # Menghapus Angka
    text = re.sub("\S*\d\S*", "", text).strip()
    text = re.sub(r"\b\d+\b", " ", text)
    
    # Mengubah text menjadi lowercase
    text = text.lower()
    
    # Menghapus white space
    text = re.sub('[\s]+', ' ', text)
    
    return text

**Proses Lemmatization**

In [7]:
!pip install nlp-id

     |████████████████████████████████| 7.9 MB 2.6 MB/s 
     |████████████████████████████████| 7.0 MB 42.6 MB/s 
     |████████████████████████████████| 1.5 MB 48.1 MB/s 
  Created wheel for nlp-id: filename=nlp_id-0.1.12.0-py3-none-any.whl size=8074105 sha256=1a064b4b349cc22d416c13ce3ffc15a5c518de0d59dd5250cf92cb712566e735
  Stored in directory: /root/.cache/pip/wheels/b2/50/48/da59531125bd94f48dfe66140f41d8fd8a4f04062050375013
  Created wheel for nltk: filename=nltk-3.4.5-py3-none-any.whl size=1449919 sha256=a534eb95858d4fdb4a9d998b31f9a968e244908ad5c40de42f6e4dda1ac5c243
  Stored in directory: /root/.cache/pip/wheels/48/8b/7f/473521e0c731c6566d631b281f323842bbda9bd819eb9a3ead
  Created wheel for wget: filename=wget-3.2-py3-none-any.whl size=9672 sha256=9a5450b0ed12b9d28f3895f21065a816f1a17bc9530f4ec38e6579e3196ed985
  Stored in directory: /root/.cache/pip/wheels/a1/b6/7c/0e63e34eb06634181c63adacca38b79ff8f35c37e3c13e3c02
Successfully built nlp-id nltk wget
  Attempting uninstall: 

In [8]:
from nlp_id.lemmatizer import Lemmatizer 
lemmatizer = Lemmatizer() 
print(tweet[11])
tweet[11]=lemmatizer.lemmatize(tweet[11]) 
tweet[11]

Batal nyoblos, baru tau ternyata ga ada no.1 di kertas suara. #AHY #kangen #mosing	


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


'batal nyoblos baru tau nyata ga ada no 1 di kertas suara ahy kangen mosing'

**Proses Stemming**

In [9]:
!pip install PySastrawi

     |████████████████████████████████| 210 kB 2.7 MB/s 


In [10]:
from Sastrawi.Stemmer.StemmerFactory import StemmerFactory

# Membuat stemmer
factory = StemmerFactory()
stemmer = factory.create_stemmer()
print(tweet[12])

tweet[12] = stemmer.stem(tweet[12])
tweet[12]

sudah boleh Ngakak? survey mu jauh panggang dari api ! #Ahy


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


'sudah boleh ngakak survey mu jauh panggang dari api ahy'

**Proses Memfilter Slang Words**

In [11]:
slang_dictionary = pd.read_csv('https://raw.githubusercontent.com/nikovs/data-science-portfolio/master/topic%20modelling/colloquial-indonesian-lexicon.csv')
slang_dict = pd.Series(slang_dictionary['formal'].values,index=slang_dictionary['slang']).to_dict()

In [12]:
def Slangwords(text):
    for word in text.split():
        if word in slang_dict.keys():
            text = text.replace(word, slang_dict[word])
    return text

In [13]:
print(tweet[10])

tweet[10] = Slangwords(tweet[10])
tweet[10]

dammnn,!! politik cantik #SBY ngorbanin #AHY


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


'dammnn,!! politik cantik #SBY mengorbankan #AHY'

**Proses Stopword**

In [14]:
from nlp_id.stopword import StopWord 
stopword = StopWord() 

In [15]:
from nlp_id.stopword import StopWord 
print(tweet[340])

tweet[340]=stopword.remove_stopword(tweet[340])
tweet[340]

Kafirrrrrr dan menista ya??!#SaveAhok #RIPJUSTICEINDONESIA #Ahok #AhokDjarot â€” iqra, iqra, iqra !!! http://www.nu.or.id


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


'Kafirrrrrr menista??!#SaveAhok#RIPJUSTICEINDONESIA#Ahok#AhokDjarotâ€” iqra, iqra, iqra!!! http://www. nu. or. id'

**Testing Menerapkan ke Semua Langkah**

In [16]:
twit_sentimen['content_processed'] = ''

for i, row in twit_sentimen.iterrows():
  content = tweet[i]
  result = Case_Folding(content)
  result = lemmatizer.lemmatize(result)
  result = stemmer.stem(result)
  result = Slangwords(result)
  result = stopword.remove_stopword(result)
  twit_sentimen['content_processed'][i] = result

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.


In [17]:
twit_bersih = twit_sentimen[['Sentiment', 'Pasangan_Calon', 'content_processed']]
twit_bersih

Sentiment Pasangan_Calon                                  content_processed
0    negative     Agus-Sylvi  akun kloning dukung agussilvy serang paslon an...
1    negative     Agus-Sylvi     agussilvy bicara kasihan lap air mata wkwkwkwk
2    negative     Agus-Sylvi  enggak memenunggu hasil qc memenunggu motif cu...
3    negative     Agus-Sylvi  kasihh oh kasihh peluru rw agussilvy mempan me...
4    negative     Agus-Sylvi  maaf dukung agussilvy hayo dukung aniessandi p...
..        ...            ...                                                ...
895  positive    Anies-Sandi  bpk aniesbaswedan sandiuno lihat rspun selfie ...
896  positive    Anies-Sandi  rangkul orang batas usia kelamin okeoce ok han...
897  positive    Anies-Sandi  jago bidang digital smiling face with sunglass...
898  positive    Anies-Sandi                                  pesanbijak okeoce
899  positive    Anies-Sandi  sandiaga bangun rumah dp simpel banding tol ci...

[900 rows x 3 columns]

In [18]:
twit_bersih.to_csv('twit_bersih.csv', index = False)
clean_tweet = pd.read_csv('twit_bersih.csv', encoding = 'latin1')
clean_tweet.head()

Sentiment Pasangan_Calon                                  content_processed
0  negative     Agus-Sylvi  akun kloning dukung agussilvy serang paslon an...
1  negative     Agus-Sylvi     agussilvy bicara kasihan lap air mata wkwkwkwk
2  negative     Agus-Sylvi  enggak memenunggu hasil qc memenunggu motif cu...
3  negative     Agus-Sylvi  kasihh oh kasihh peluru rw agussilvy mempan me...
4  negative     Agus-Sylvi  maaf dukung agussilvy hayo dukung aniessandi p...

**Note: INGAT INGAT NAMA DATASET YANG BAKAL DIPAKE DI BoW = CLEAN_TWEET**

## Try TF IDF

In [19]:
#Impor Modul Yang Diperlukan
import pandas as pd
import numpy as np
from nltk.tokenize import word_tokenize
import math
from sklearn.preprocessing import normalize
import nltk
from nltk.tokenize import word_tokenize
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [20]:
clean_tweet

Sentiment Pasangan_Calon                                  content_processed
0    negative     Agus-Sylvi  akun kloning dukung agussilvy serang paslon an...
1    negative     Agus-Sylvi     agussilvy bicara kasihan lap air mata wkwkwkwk
2    negative     Agus-Sylvi  enggak memenunggu hasil qc memenunggu motif cu...
3    negative     Agus-Sylvi  kasihh oh kasihh peluru rw agussilvy mempan me...
4    negative     Agus-Sylvi  maaf dukung agussilvy hayo dukung aniessandi p...
..        ...            ...                                                ...
895  positive    Anies-Sandi  bpk aniesbaswedan sandiuno lihat rspun selfie ...
896  positive    Anies-Sandi  rangkul orang batas usia kelamin okeoce ok han...
897  positive    Anies-Sandi  jago bidang digital smiling face with sunglass...
898  positive    Anies-Sandi                                  pesanbijak okeoce
899  positive    Anies-Sandi  sandiaga bangun rumah dp simpel banding tol ci...

[900 rows x 3 columns]

In [21]:
# MEMBUAT LIST KOSA KATA

kosa_kata = set()
for i in clean_tweet.content_processed:
    token_kal=set(word_tokenize(i.lower()))
    kosa_kata=set.union(kosa_kata,token_kal)
    #print(kosa_kata)
    
kosa_kata = sorted(kosa_kata)
print(kosa_kata)

# Jumlah kata-kata pada list vocab           
jumlah_kosa_kata = len(kosa_kata)
print(jumlah_kosa_kata)

['a', 'aa', 'aagym', 'abaaah', 'abal', 'abang', 'abdi', 'absurd', 'abunawas', 'aburizal', 'abused', 'acara', 'acu', 'adaaqua', 'adalahkita', 'addiems', 'adekku', 'adil', 'adjierimbawan', 'adjrot', 'agam', 'agama', 'agllusylludhoyono', 'agus', 'agusharimurtiyudhoyono', 'agussilvy', 'agussylvi', 'agusyudhoyono', 'ah', 'aher', 'ahli', 'ahmadfuadanwar', 'ahok', 'ahokbtp', 'ahokdicintairakyat', 'ahokdjarot', 'ahokdjarota', 'ahokdjarotdirosi', 'ahokdjarotlebihbaik', 'ahokdjarotmenang', 'ahoker', 'ahokers', 'ahokfornobel', 'ahokfree', 'ahokhebat', 'ahokishope', 'ahokjarot', 'ahokkalah', 'ahokkeok', 'ahoklovers', 'ahokmandikembang', 'ahokmartir', 'ahokmenang', 'ahokpanikahokkalah', 'ahokpenistaagama', 'ahokrekormuri', 'ahokselaludihati', 'ahokshow', 'ahoktakbersalah', 'ahoktumbang', 'ahox', 'ahy', 'ahya', 'ahyaforall', 'ahyahargamati', 'ahycenter', 'ahyfansclub', 'ahyforall', 'ahylovers', 'ahymaininsara', 'ahysylvi', 'aib', 'aiman', 'air', 'ajak', 'ajang', 'ajar', 'aji', 'ajibarang', 'aka', 'a

In [22]:
indeks_kata = {}
for kata in kosa_kata:
    indeks_kata[kata] = 0
    
print(indeks_kata)

{'a': 0, 'aa': 0, 'aagym': 0, 'abaaah': 0, 'abal': 0, 'abang': 0, 'abdi': 0, 'absurd': 0, 'abunawas': 0, 'aburizal': 0, 'abused': 0, 'acara': 0, 'acu': 0, 'adaaqua': 0, 'adalahkita': 0, 'addiems': 0, 'adekku': 0, 'adil': 0, 'adjierimbawan': 0, 'adjrot': 0, 'agam': 0, 'agama': 0, 'agllusylludhoyono': 0, 'agus': 0, 'agusharimurtiyudhoyono': 0, 'agussilvy': 0, 'agussylvi': 0, 'agusyudhoyono': 0, 'ah': 0, 'aher': 0, 'ahli': 0, 'ahmadfuadanwar': 0, 'ahok': 0, 'ahokbtp': 0, 'ahokdicintairakyat': 0, 'ahokdjarot': 0, 'ahokdjarota': 0, 'ahokdjarotdirosi': 0, 'ahokdjarotlebihbaik': 0, 'ahokdjarotmenang': 0, 'ahoker': 0, 'ahokers': 0, 'ahokfornobel': 0, 'ahokfree': 0, 'ahokhebat': 0, 'ahokishope': 0, 'ahokjarot': 0, 'ahokkalah': 0, 'ahokkeok': 0, 'ahoklovers': 0, 'ahokmandikembang': 0, 'ahokmartir': 0, 'ahokmenang': 0, 'ahokpanikahokkalah': 0, 'ahokpenistaagama': 0, 'ahokrekormuri': 0, 'ahokselaludihati': 0, 'ahokshow': 0, 'ahoktakbersalah': 0, 'ahoktumbang': 0, 'ahox': 0, 'ahy': 0, 'ahya': 0, 'a

In [23]:
# MEMBUAT MATRIKS TF

In [24]:
vektor_TF=np.array([])
for baris_teks in clean_tweet.content_processed:
    print(baris_teks)
    baris_kata = indeks_kata.copy()
    print('baris_kata', baris_kata)
    split_baris = baris_teks.lower().split()
    for kata in baris_teks.lower().split():
        baris_kata[kata]=+1
        print(baris_kata)
    baris_kata = np.array(list(baris_kata.values()))
    baris_kata = baris_kata/len(split_baris)
    vektor_TF = np.concatenate((vektor_TF,baris_kata), axis=0)
    print(vektor_TF)
matriks_TF = vektor_TF.reshape(clean_tweet.shape[0], jumlah_kosa_kata)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'a': 0, 'aa': 0, 'aagym': 0, 'abaaah': 0, 'abal': 0, 'abang': 0, 'abdi': 0, 'absurd': 0, 'abunawas': 0, 'aburizal': 0, 'abused': 0, 'acara': 0, 'acu': 0, 'adaaqua': 0, 'adalahkita': 0, 'addiems': 0, 'adekku': 0, 'adil': 0, 'adjierimbawan': 0, 'adjrot': 0, 'agam': 0, 'agama': 0, 'agllusylludhoyono': 0, 'agus': 1, 'agusharimurtiyudhoyono': 0, 'agussilvy': 0, 'agussylvi': 0, 'agusyudhoyono': 0, 'ah': 0, 'aher': 0, 'ahli': 0, 'ahmadfuadanwar': 0, 'ahok': 0, 'ahokbtp': 0, 'ahokdicintairakyat': 0, 'ahokdjarot': 0, 'ahokdjarota': 0, 'ahokdjarotdirosi': 0, 'ahokdjarotlebihbaik': 0, 'ahokdjarotmenang': 0, 'ahoker': 0, 'ahokers': 0, 'ahokfornobel': 0, 'ahokfree': 0, 'ahokhebat': 0, 'ahokishope': 0, 'ahokjarot': 0, 'ahokkalah': 0, 'ahokkeok': 0, 'ahoklovers': 0, 'ahokmandikembang': 0, 'ahokmartir': 0, 'ahokmenang': 0, 'ahokpanikahokkalah': 0, 'ahokpenistaagama': 0, 'ahokrekormuri': 0, 'ahokselaludihati': 0, 'ahokshow': 0, 'ahoktakbersalah': 0, 'ahoktumbang': 0, 'ahox': 0, 'ahy': 1, 'ahya': 0, 'a

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[0. 0. 0. ... 0. 0. 0.]
curiga saldo kenti blt orang curiga mekanisme ahy
baris_kata {'a': 0, 'aa': 0, 'aagym': 0, 'abaaah': 0, 'abal': 0, 'abang': 0, 'abdi': 0, 'absurd': 0, 'abunawas': 0, 'aburizal': 0, 'abused': 0, 'acara': 0, 'acu': 0, 'adaaqua': 0, 'adalahkita': 0, 'addiems': 0, 'adekku': 0, 'adil': 0, 'adjierimbawan': 0, 'adjrot': 0, 'agam': 0, 'agama': 0, 'agllusylludhoyono': 0, 'agus': 0, 'agusharimurtiyudhoyono': 0, 'agussilvy': 0, 'agussylvi': 0, 'agusyudhoyono': 0, 'ah': 0, 'aher': 0, 'ahli': 0, 'ahmadfuadanwar': 0, 'ahok': 0, 'ahokbtp': 0, 'ahokdicintairakyat': 0, 'ahokdjarot': 0, 'ahokdjarota': 0, 'ahokdjarotdirosi': 0, 'ahokdjarotlebihbaik': 0, 'ahokdjarotmenang': 0, 'ahoker': 0, 'ahokers': 0, 'ahokfornobel': 0, 'ahokfree': 0, 'ahokhebat': 0, 'ahokishope': 0, 'ahokjarot': 0, 'ahokkalah': 0, 'ahokkeok': 0, 'ahoklovers': 0, 'ahokmandikembang': 0, 'ahokmartir': 0, 'ahokmenang': 0, 'ahokpanikahokkalah': 0, 'ahokpenistaagama': 0, 'ahokrekormuri': 0, 'ahokselaludihati': 0, 'aho

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



...


[0. 0. 0. ... 0. 0. 0.]
keren ahy
baris_kata {'a': 0, 'aa': 0, 'aagym': 0, 'abaaah': 0, 'abal': 0, 'abang': 0, 'abdi': 0, 'absurd': 0, 'abunawas': 0, 'aburizal': 0, 'abused': 0, 'acara': 0, 'acu': 0, 'adaaqua': 0, 'adalahkita': 0, 'addiems': 0, 'adekku': 0, 'adil': 0, 'adjierimbawan': 0, 'adjrot': 0, 'agam': 0, 'agama': 0, 'agllusylludhoyono': 0, 'agus': 0, 'agusharimurtiyudhoyono': 0, 'agussilvy': 0, 'agussylvi': 0, 'agusyudhoyono': 0, 'ah': 0, 'aher': 0, 'ahli': 0, 'ahmadfuadanwar': 0, 'ahok': 0, 'ahokbtp': 0, 'ahokdicintairakyat': 0, 'ahokdjarot': 0, 'ahokdjarota': 0, 'ahokdjarotdirosi': 0, 'ahokdjarotlebihbaik': 0, 'ahokdjarotmenang': 0, 'ahoker': 0, 'ahokers': 0, 'ahokfornobel': 0, 'ahokfree': 0, 'ahokhebat': 0, 'ahokishope': 0, 'ahokjarot': 0, 'ahokkalah': 0, 'ahokkeok': 0, 'ahoklovers': 0, 'ahokmandikembang': 0, 'ahokmartir': 0, 'ahokmenang': 0, 'ahokpanikahokkalah': 0, 'ahokpenistaagama': 0, 'ahokrekormuri': 0, 'ahokselaludihati': 0, 'ahokshow': 0, 'ahoktakbersalah': 0, 'ahokt

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[0. 0. 0. ... 0. 0. 0.]
ahy
baris_kata {'a': 0, 'aa': 0, 'aagym': 0, 'abaaah': 0, 'abal': 0, 'abang': 0, 'abdi': 0, 'absurd': 0, 'abunawas': 0, 'aburizal': 0, 'abused': 0, 'acara': 0, 'acu': 0, 'adaaqua': 0, 'adalahkita': 0, 'addiems': 0, 'adekku': 0, 'adil': 0, 'adjierimbawan': 0, 'adjrot': 0, 'agam': 0, 'agama': 0, 'agllusylludhoyono': 0, 'agus': 0, 'agusharimurtiyudhoyono': 0, 'agussilvy': 0, 'agussylvi': 0, 'agusyudhoyono': 0, 'ah': 0, 'aher': 0, 'ahli': 0, 'ahmadfuadanwar': 0, 'ahok': 0, 'ahokbtp': 0, 'ahokdicintairakyat': 0, 'ahokdjarot': 0, 'ahokdjarota': 0, 'ahokdjarotdirosi': 0, 'ahokdjarotlebihbaik': 0, 'ahokdjarotmenang': 0, 'ahoker': 0, 'ahokers': 0, 'ahokfornobel': 0, 'ahokfree': 0, 'ahokhebat': 0, 'ahokishope': 0, 'ahokjarot': 0, 'ahokkalah': 0, 'ahokkeok': 0, 'ahoklovers': 0, 'ahokmandikembang': 0, 'ahokmartir': 0, 'ahokmenang': 0, 'ahokpanikahokkalah': 0, 'ahokpenistaagama': 0, 'ahokrekormuri': 0, 'ahokselaludihati': 0, 'ahokshow': 0, 'ahoktakbersalah': 0, 'ahoktumbang'

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[0. 0. 0. ... 0. 0. 0.]
jago bidang digital smiling face with sunglasses ok hand thonyleong com okeoce salambersama
baris_kata {'a': 0, 'aa': 0, 'aagym': 0, 'abaaah': 0, 'abal': 0, 'abang': 0, 'abdi': 0, 'absurd': 0, 'abunawas': 0, 'aburizal': 0, 'abused': 0, 'acara': 0, 'acu': 0, 'adaaqua': 0, 'adalahkita': 0, 'addiems': 0, 'adekku': 0, 'adil': 0, 'adjierimbawan': 0, 'adjrot': 0, 'agam': 0, 'agama': 0, 'agllusylludhoyono': 0, 'agus': 0, 'agusharimurtiyudhoyono': 0, 'agussilvy': 0, 'agussylvi': 0, 'agusyudhoyono': 0, 'ah': 0, 'aher': 0, 'ahli': 0, 'ahmadfuadanwar': 0, 'ahok': 0, 'ahokbtp': 0, 'ahokdicintairakyat': 0, 'ahokdjarot': 0, 'ahokdjarota': 0, 'ahokdjarotdirosi': 0, 'ahokdjarotlebihbaik': 0, 'ahokdjarotmenang': 0, 'ahoker': 0, 'ahokers': 0, 'ahokfornobel': 0, 'ahokfree': 0, 'ahokhebat': 0, 'ahokishope': 0, 'ahokjarot': 0, 'ahokkalah': 0, 'ahokkeok': 0, 'ahoklovers': 0, 'ahokmandikembang': 0, 'ahokmartir': 0, 'ahokmenang': 0, 'ahokpanikahokkalah': 0, 'ahokpenistaagama': 0, 'ahok

In [25]:
print(matriks_TF)

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


In [26]:
df_TF = pd.DataFrame(matriks_TF, columns=kosa_kata, index=clean_tweet.content_processed.tolist())
df_TF

a   aa  ...  zipper  zona
akun kloning dukung agussilvy serang paslon ani...  0.0  0.0  ...     0.0   0.0
agussilvy bicara kasihan lap air mata wkwkwkwk      0.0  0.0  ...     0.0   0.0
enggak memenunggu hasil qc memenunggu motif cui...  0.0  0.0  ...     0.0   0.0
kasihh oh kasihh peluru rw agussilvy mempan men...  0.0  0.0  ...     0.0   0.0
maaf dukung agussilvy hayo dukung aniessandi pu...  0.0  0.0  ...     0.0   0.0
...                                                 ...  ...  ...     ...   ...
bpk aniesbaswedan sandiuno lihat rspun selfie o...  0.0  0.0  ...     0.0   0.0
rangkul orang batas usia kelamin okeoce ok hand...  0.0  0.0  ...     0.0   0.0
jago bidang digital smiling face with sunglasse...  0.0  0.0  ...     0.0   0.0
pesanbijak okeoce                                   0.0  0.0  ...     0.0   0.0
sandiaga bangun rumah dp simpel banding tol cip...  0.0  0.0  ...     0.0   0.0

[900 rows x 2503 columns]

In [27]:
# MEMBUAT BARIS IDF

In [28]:
baris_IDF=[]
for kolom in df_TF.columns :
    N = len(clean_tweet.content_processed)
    kal_kata = len(df_TF[df_TF[kolom]>0])
    baris_idf = (math.log((1+N)/(1+kal_kata)))+1  
    baris_IDF.append(baris_idf)
baris_IDF

[4.970291913552122,
 6.417210896488447,
 6.704892968940229,
 7.110358077048392,
 7.110358077048392,
 6.704892968940229,
 7.110358077048392,
 7.110358077048392,
 7.110358077048392,
 7.110358077048392,
 7.110358077048392,
 6.194067345174237,
 7.110358077048392,
 6.704892968940229,
 7.110358077048392,
 6.194067345174237,
 7.110358077048392,
 5.238555900146801,
 7.110358077048392,
 7.110358077048392,
 7.110358077048392,
 5.16444792799308,
 7.110358077048392,
 4.970291913552122,
 7.110358077048392,
 4.859066278441897,
 7.110358077048392,
 4.712462804250022,
 6.417210896488447,
 7.110358077048392,
 7.110358077048392,
 7.110358077048392,
 2.74725945226003,
 7.110358077048392,
 6.011745788380283,
 2.4469189829363254,
 6.194067345174237,
 6.011745788380283,
 7.110358077048392,
 7.110358077048392,
 5.857595108553024,
 5.724063715928502,
 6.704892968940229,
 6.704892968940229,
 7.110358077048392,
 5.857595108553024,
 7.110358077048392,
 7.110358077048392,
 7.110358077048392,
 7.110358077048392,
 

In [29]:
# MEMBUAT MATRIKS TD-IDF

In [30]:
vektor_TFIDF=np.array([])
for baris in matriks_TF:
    baris_tfidf=np.multiply(baris,baris_IDF)
    vektor_TFIDF=np.concatenate((vektor_TFIDF,baris_tfidf), axis=0)
    
matriks_TFIDF = vektor_TFIDF.reshape(clean_tweet.shape[0], jumlah_kosa_kata)
matriks_TFIDF = normalize(matriks_TFIDF)

In [31]:
# MEMBUAT DATAFRAME TFIDF

In [32]:
df_TF_IDF = pd.DataFrame(matriks_TFIDF, columns=kosa_kata, index=clean_tweet.content_processed.tolist())
df_TF_IDF

a   aa  ...  zipper  zona
akun kloning dukung agussilvy serang paslon ani...  0.0  0.0  ...     0.0   0.0
agussilvy bicara kasihan lap air mata wkwkwkwk      0.0  0.0  ...     0.0   0.0
enggak memenunggu hasil qc memenunggu motif cui...  0.0  0.0  ...     0.0   0.0
kasihh oh kasihh peluru rw agussilvy mempan men...  0.0  0.0  ...     0.0   0.0
maaf dukung agussilvy hayo dukung aniessandi pu...  0.0  0.0  ...     0.0   0.0
...                                                 ...  ...  ...     ...   ...
bpk aniesbaswedan sandiuno lihat rspun selfie o...  0.0  0.0  ...     0.0   0.0
rangkul orang batas usia kelamin okeoce ok hand...  0.0  0.0  ...     0.0   0.0
jago bidang digital smiling face with sunglasse...  0.0  0.0  ...     0.0   0.0
pesanbijak okeoce                                   0.0  0.0  ...     0.0   0.0
sandiaga bangun rumah dp simpel banding tol cip...  0.0  0.0  ...     0.0   0.0

[900 rows x 2503 columns]

In [33]:
# MEMBUAT FUNGSI TFIDF()

#Impor Modul Yang Diperlukan
import pandas as pd
import numpy as np
from nltk.tokenize import word_tokenize
import math
from sklearn.preprocessing import normalize

def TF_IDF(df_teks):
    # Membuat list kosa kata dari seluruh teks input
    kosa_kata = set()
    for i in clean_tweet.content_processed:
        token_kal=set(word_tokenize(i.lower()))
        kosa_kata=set.union(kosa_kata,token_kal)
    kosa_kata = sorted(kosa_kata)
    # Membuat dictionary kata-kata
    indeks_kata = {}
    for kata in kosa_kata:
        indeks_kata[kata] = 0
    # Jumlah kosa kata(untuk kolom)
    jumlah_kosa_kata = len(kosa_kata)
    # Membagun matriks kata TF
    vektor_TF=np.array([])
    for baris_teks in clean_tweet.content_processed:
        baris_kata = indeks_kata.copy()
        split_baris = baris_teks.lower().split()
        for kata in baris_teks.lower().split():
            baris_kata[kata]=+1
        baris_kata = np.array(list(baris_kata.values()))
        baris_kata = baris_kata/len(split_baris)
        vektor_TF = np.concatenate((vektor_TF,baris_kata), axis=0)
    matriks_TF = vektor_TF.reshape(clean_tweet.shape[0], jumlah_kosa_kata)
    # Membagun dataframe kata TF
    df_TF = pd.DataFrame(matriks_TF, columns=kosa_kata, index=clean_tweet.content_processed.tolist())
    # Menghitung baris IDF
    baris_IDF=[]
    for kolom in df_TF.columns :
        N = len(clean_tweet.content_processed)
        kal_kata = len(df_TF[df_TF[kolom]>0])
        baris_idf = (math.log((1+N)/(1+kal_kata)))+1  
        baris_IDF.append(baris_idf)
    # Membuat matriks TF-IDF
    vektor_TFIDF=np.array([])
    for baris in matriks_TF:
        baris_tfidf=np.multiply(baris,baris_IDF)
        vektor_TFIDF=np.concatenate((vektor_TFIDF,baris_tfidf), axis=0)
    matriks_TFIDF = vektor_TFIDF.reshape(df_teks.shape[0], jumlah_kosa_kata)
    matriks_TFIDF = normalize(matriks_TFIDF)
    # Membuat dataframe TF-IDF
    df_TF_IDF = pd.DataFrame(matriks_TFIDF, columns=kosa_kata, index=clean_tweet.content_processed.tolist())
    return df_TF_IDF

In [34]:
# CONTOH IMPLEMENTASU FUNGSI TF_IDF()

clean_tweet

Sentiment Pasangan_Calon                                  content_processed
0    negative     Agus-Sylvi  akun kloning dukung agussilvy serang paslon an...
1    negative     Agus-Sylvi     agussilvy bicara kasihan lap air mata wkwkwkwk
2    negative     Agus-Sylvi  enggak memenunggu hasil qc memenunggu motif cu...
3    negative     Agus-Sylvi  kasihh oh kasihh peluru rw agussilvy mempan me...
4    negative     Agus-Sylvi  maaf dukung agussilvy hayo dukung aniessandi p...
..        ...            ...                                                ...
895  positive    Anies-Sandi  bpk aniesbaswedan sandiuno lihat rspun selfie ...
896  positive    Anies-Sandi  rangkul orang batas usia kelamin okeoce ok han...
897  positive    Anies-Sandi  jago bidang digital smiling face with sunglass...
898  positive    Anies-Sandi                                  pesanbijak okeoce
899  positive    Anies-Sandi  sandiaga bangun rumah dp simpel banding tol ci...

[900 rows x 3 columns]

In [35]:
df_TF_IDF=TF_IDF(clean_tweet)

# Export ke CSV
df_TF_IDF.to_csv('Pilkada_DKI_TFIDF.csv', index=False)

df_TF_IDF

a   aa  ...  zipper  zona
akun kloning dukung agussilvy serang paslon ani...  0.0  0.0  ...     0.0   0.0
agussilvy bicara kasihan lap air mata wkwkwkwk      0.0  0.0  ...     0.0   0.0
enggak memenunggu hasil qc memenunggu motif cui...  0.0  0.0  ...     0.0   0.0
kasihh oh kasihh peluru rw agussilvy mempan men...  0.0  0.0  ...     0.0   0.0
maaf dukung agussilvy hayo dukung aniessandi pu...  0.0  0.0  ...     0.0   0.0
...                                                 ...  ...  ...     ...   ...
bpk aniesbaswedan sandiuno lihat rspun selfie o...  0.0  0.0  ...     0.0   0.0
rangkul orang batas usia kelamin okeoce ok hand...  0.0  0.0  ...     0.0   0.0
jago bidang digital smiling face with sunglasse...  0.0  0.0  ...     0.0   0.0
pesanbijak okeoce                                   0.0  0.0  ...     0.0   0.0
sandiaga bangun rumah dp simpel banding tol cip...  0.0  0.0  ...     0.0   0.0

[900 rows x 2503 columns]